In [13]:
import os
import random
import json
import pickle
from copy import deepcopy
from tqdm import tqdm
from collections import defaultdict

import numpy as np
from transformers import BertTokenizerFast

In [14]:
import os

# 定义数据集名称列表
datasets = ["arxiv", "wikics", "reddit", "instagram"]
base_path = "/home/yuhanli/GLBench/models/alignment/Patton/data"

# 遍历每个数据集，为每个数据集创建指定的文件夹
for dataset in datasets:
    # 构建每个数据集的基本路径
    dataset_path = os.path.join(base_path, dataset)
    
    # 定义需要创建的子文件夹名称
    subfolders = ["nc", "nc-coarse", "neighbor", "self-train"]
    
    # 遍历并创建每个子文件夹
    for folder in subfolders:
        # 构建完整的文件夹路径
        folder_path = os.path.join(dataset_path, folder)
        
        # 如果文件夹不存在，则创建它
        if not os.path.exists(folder_path):
            os.makedirs(folder_path)
            print(f"创建文件夹: {folder_path}")
        else:
            print(f"文件夹已存在: {folder_path}")

文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/arxiv/nc
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/arxiv/nc-coarse
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/arxiv/neighbor
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/arxiv/self-train
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/wikics/nc
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/wikics/nc-coarse
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/wikics/neighbor
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/wikics/self-train
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/reddit/nc
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/reddit/nc-coarse
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/reddit/neighbor
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/reddit/self-train
文件夹已存在: /home/yuhanli/GLBench/models/alignment/Patton/data/instagram/nc
文件夹已存在: /home/yuhanli/GLBench/models/alig

In [15]:
random.seed(0)

In [16]:
# dataset = 'MAG' 
# sub_dataset='Mathematics'
dataset = 'arxiv' 

# Generate Pretraining Data

In [17]:
#GLBench
import torch
datasets= torch.load(f'../../../../datasets/{dataset}.pt')
data_text = datasets.raw_texts

data = {i: text for i, text in tqdm(enumerate(data_text))}

169343it [00:00, 2592068.51it/s]


In [18]:
datasets= torch.load(f'../../../../datasets/{dataset}.pt')
datasets.edge_index

tensor([[104447,  15858, 107156,  ...,  45118,  45118,  45118],
        [ 13091,  47283,  69161,  ..., 162473, 162537,  72717]])

In [19]:
# # read label name dict
# label_name_dict = {}
# label_name_set = set()
# label_name2id_dict = {}

# with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/Mathematics/labels.txt') as f:
#     readin = f.readlines()
#     for line in tqdm(readin):
#         tmp = line.strip().split('\t')
#         label_name_dict[tmp[0]] = tmp[1]
#         label_name2id_dict[tmp[1]] = tmp[0]
#         label_name_set.add(tmp[1])

# print(f'Num of unique labels:{len(label_name_set)}')

In [20]:
label_name_set = datasets.label_name

In [21]:
# # filter related

# idd_set = set(list(data.keys()))

# for idd in tqdm(data):
#     if 'reference' not in data[idd] or len(data[idd]['reference']) == 0:
#         continue
        
#     data[idd]['reference'] = list(set(data[idd]['reference']) & idd_set)

In [22]:
# # text processing function
# def text_process(text):
#     p_text = ' '.join(text.split('\r\n'))
#     p_text = ' '.join(p_text.split('\n\r'))
#     p_text = ' '.join(p_text.split('\n'))
#     p_text = ' '.join(p_text.split('\t'))
#     p_text = ' '.join(p_text.split('\rm'))
#     p_text = ' '.join(p_text.split('\r'))
#     p_text = ''.join(p_text.split('$'))
#     p_text = ''.join(p_text.split('*'))

#     return p_text

In [23]:
# average edge

# ref_cnt = 0
# ref_paper = {}


# for idd in tqdm(data):
#     if 'reference' not in data[idd] or len(data[idd]['reference']) == 0:
#         continue
        
#     ref_cnt += len(data[idd]['reference'])
#     ref_paper[idd] = data[idd]

# print(f'avg ref cnt:{ref_cnt/len(ref_paper)}.')
# print(f'ref papers:{len(ref_paper)}')

In [24]:
ref_paper=data

In [25]:
edge_index = np.array(datasets.edge_index)# 创建一个字典来保存每个节点的邻居
neighbors = defaultdict(list)
for start_node, end_node in zip(edge_index[0], edge_index[1]):
    neighbors[start_node].append(end_node)
neighbors

defaultdict(list,
            {104447: [13091],
             15858: [47283],
             107156: [69161, 136440, 107366, 158460],
             141536: [90124, 121740, 122427, 161023, 84342],
             82077: [19879, 147042, 35436],
             31735: [21375],
             42436: [90249, 32625],
             141537: [6591],
             27755: [67879, 102869],
             88685: [11734, 150492, 26107, 148059],
             19875: [102033],
             124316: [66343, 80759],
             93960: [162918, 79085],
             82078: [49187, 20075, 120025, 81746, 52854, 153223],
             23846: [141566],
             157506: [10578],
             58394: [134600, 73960, 44773, 16921],
             160132: [69161, 67226, 80377],
             79476: [49267, 88828, 51904, 76403],
             124317: [65092, 131082, 24696, 20726, 23478, 154492],
             6447: [143121],
             97929: [65066, 76382, 52615, 4907],
             80756: [104499],
             149644: [148061],


In [26]:
## split train/val/test as 8:1:1

random.seed(0)

train_pairs = []
val_pairs = []
test_pairs = []
train_pair_set = set()
item_id2idx = {}
train_neighbor = defaultdict(list)
val_neighbor = defaultdict(list)
test_neighbor = defaultdict(list)

# 假设 edge_index 是一个 numpy 数组或类似的结构，形状为 (2, E) 其中 E 是边的数量
import numpy as np
edge_index = np.array(datasets.edge_index)# 创建一个字典来保存每个节点的邻居
neighbors = defaultdict(list)
for start_node, end_node in zip(edge_index[0], edge_index[1]):
    neighbors[start_node].append(end_node)

# 现在可以使用 neighbors 字典来代替 ref_paper[iid]['reference']
for iid in tqdm(ref_paper):
    if iid not in item_id2idx:
        item_id2idx[iid] = len(item_id2idx)
    
    also_viewed = neighbors[iid]  # 使用从 edge_index 得到的邻居列表
    # random.shuffle(also_viewed)
    
    for i in range(int(len(also_viewed)*0.8)):
        train_pairs.append((iid, also_viewed[i]))
        train_pair_set.add((iid, also_viewed[i]))
        train_pair_set.add((also_viewed[i], iid))
        
        if also_viewed[i] not in item_id2idx:
            item_id2idx[also_viewed[i]] = len(item_id2idx)

        train_neighbor[iid].append(also_viewed[i])

    for i in range(int(len(also_viewed)*0.8), int(len(also_viewed)*0.9)):
        if (iid, also_viewed[i]) in train_pair_set:
            continue
        val_pairs.append((iid, also_viewed[i]))
        assert (iid, also_viewed[i]) not in train_pair_set

        if also_viewed[i] not in item_id2idx:
            item_id2idx[also_viewed[i]] = len(item_id2idx)
        
        val_neighbor[iid].append(also_viewed[i])
        
    for i in range(int(len(also_viewed)*0.9), len(also_viewed)):
        if (iid, also_viewed[i]) in train_pair_set:
            continue
        test_pairs.append((iid, also_viewed[i]))
        assert (iid, also_viewed[i]) not in train_pair_set
        
        if also_viewed[i] not in item_id2idx:
            item_id2idx[also_viewed[i]] = len(item_id2idx)
        
        test_neighbor[iid].append(also_viewed[i])
        
print(f'Train/Val/Test size:{len(train_pairs)},{len(val_pairs)},{len(test_pairs)}')
print(f'Train/Val/Test avg:{len(train_pairs)/len(ref_paper)},{len(val_pairs)/len(ref_paper)},{len(test_pairs)/len(ref_paper)}')

100%|██████████| 169343/169343 [00:02<00:00, 61987.01it/s]

Train/Val/Test size:859718,98435,206612
Train/Val/Test avg:5.076784986683831,0.5812758720466745,1.2200799560655002


In [27]:
# save all the text on node in the graph

node_id_set = set()

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/corpus.txt','w') as fout:    
    for iid in tqdm(ref_paper):
        also_viewed = neighbors
        
        # save iid text
        if iid not in node_id_set:
            node_id_set.add(iid)
            fout.write(str(iid)+'\t'+data[iid]+'\n')
    
        # save neighbor
        for iid_n in also_viewed:
            if iid_n not in node_id_set:
                node_id_set.add(iid_n)
                fout.write(str(iid_n)+'\t'+data[iid_n]+'\n')

 77%|███████▋  | 130885/169343 [30:55<10:09, 63.09it/s]

In [ ]:
sample_neighbor_num = 5

In [ ]:
# generate and save train file

random.seed(0)
sample_neighbor_num = 5

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/train.text.jsonl','w') as fout:
    for (q, k) in tqdm(train_pairs):
        q=str(q)
        k=str(k)
        # prepare sample pool for item
        q_n_pool = set(deepcopy(train_neighbor[int(q)]))
        k_n_pool = set(deepcopy(train_neighbor[int(k)]))

        if k in q_n_pool:
            q_n_pool.remove(k)
        if q in k_n_pool:
            k_n_pool.remove(q)
        q_n_pool = list(q_n_pool)
        k_n_pool = list(k_n_pool)
        # random.shuffle(q_n_pool)
        # random.shuffle(k_n_pool)
        
        # # sample neighbor
        if len(q_n_pool) >= sample_neighbor_num:
            q_samples = q_n_pool[:sample_neighbor_num]
        else:
            q_samples = q_n_pool + [-1] * (sample_neighbor_num-len(q_n_pool))
        
        if len(k_n_pool) >= sample_neighbor_num:
            k_samples = k_n_pool[:sample_neighbor_num]
        else:
            k_samples = k_n_pool + [-1] * (sample_neighbor_num-len(k_n_pool))
        
        # prepare for writing file
        q_text = data[int(q)]
        q_n_text = '\*\*'.join([data[q_n] if q_n != -1 else '' for q_n in q_samples])
        q_n_text = [data[q_n] if q_n != -1 else '' for q_n in q_samples]
        
        k_text = data[int(k)]
        #k_n_text = '\*\*'.join([text_process(data[k_n]) if k_n != -1 else '' for k_n in k_samples])
        k_n_text = [data[k_n] if k_n != -1 else '' for k_n in k_samples]
        
        #q_line = q_text + '\t' + q_n_text
        #k_line = k_text + '\t' + k_n_text
        
        #fout.write(q_line+'\t'+k_line+'\n')
        fout.write(json.dumps({
            'q_text':q_text,
            'q_n_text':q_n_text,
            'k_text':k_text,
            'k_n_text':k_n_text,
        })+'\n')

100%|██████████| 859718/859718 [01:46<00:00, 8081.16it/s] 


In [ ]:
# generate and save val file (make sure to delete items that are not in train set)

random.seed(0)

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/val.text.jsonl','w') as fout:
    for (q, k) in tqdm(val_pairs):
        
        # prepare sample pool for item
        q_n_pool = set(deepcopy(train_neighbor[q]))
        k_n_pool = set(deepcopy(train_neighbor[k]))

        if k in q_n_pool:
            q_n_pool.remove(k)
        if q in k_n_pool:
            k_n_pool.remove(q)

        q_n_pool = list(q_n_pool)
        k_n_pool = list(k_n_pool)
        # random.shuffle(q_n_pool)
        # random.shuffle(k_n_pool)
        
        # sample neighbor
        if len(q_n_pool) >= sample_neighbor_num:
            q_samples = q_n_pool[:sample_neighbor_num]
        else:
            q_samples = q_n_pool + [-1] * (sample_neighbor_num-len(q_n_pool))
        
        if len(k_n_pool) >= sample_neighbor_num:
            k_samples = k_n_pool[:sample_neighbor_num]
        else:
            k_samples = k_n_pool + [-1] * (sample_neighbor_num-len(k_n_pool))
        
        # prepare for writing file
        q_text = data[q]
        #q_n_text = '\*\*'.join([text_process(data[q_n]['title']) if q_n != -1 else '' for q_n in q_samples])
        q_n_text = [data[q_n] if q_n != -1 else '' for q_n in q_samples]
        
        k_text = data[k]
        #k_n_text = '\*\*'.join([text_process(data[k_n]['title']) if k_n != -1 else '' for k_n in k_samples])
        k_n_text = [data[k_n] if k_n != -1 else '' for k_n in k_samples]
        
        #q_line = q_text + '\t' + q_n_text
        #k_line = k_text + '\t' + k_n_text
        
        #fout.write(q_line+'\t'+k_line+'\n')
        fout.write(json.dumps({
            'q_text':q_text,
            'q_n_text':q_n_text,
            'k_text':k_text,
            'k_n_text':k_n_text,
        })+'\n')

100%|██████████| 98435/98435 [00:13<00:00, 7569.07it/s]


In [ ]:
# generate and save test file (make sure to delete items that are not in train set)

random.seed(0)

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/test.text.jsonl','w') as fout:
    for (q, k) in tqdm(test_pairs):
        
        # prepare sample pool for item
        q_n_pool = set(deepcopy(train_neighbor[q]))
        k_n_pool = set(deepcopy(train_neighbor[k]))

        if k in q_n_pool:
            q_n_pool.remove(k)
        if q in k_n_pool:
            k_n_pool.remove(q)

        q_n_pool = list(q_n_pool)
        k_n_pool = list(k_n_pool)
        # random.shuffle(q_n_pool)
        # random.shuffle(k_n_pool)
        
        # sample neighbor
        if len(q_n_pool) >= sample_neighbor_num:
            q_samples = q_n_pool[:sample_neighbor_num]
        else:
            q_samples = q_n_pool + [-1] * (sample_neighbor_num-len(q_n_pool))
        
        if len(k_n_pool) >= sample_neighbor_num:
            k_samples = k_n_pool[:sample_neighbor_num]
        else:
            k_samples = k_n_pool + [-1] * (sample_neighbor_num-len(k_n_pool))
        
        # prepare for writing file
        q_text = data[q]
        #q_n_text = '\*\*'.join([text_process(data[q_n]['title']) if q_n != -1 else '' for q_n in q_samples])
        q_n_text =[data[q_n]if q_n != -1 else '' for q_n in q_samples]
        
        k_text = data[k]
        #k_n_text = '\*\*'.join([text_process(data[k_n]['title']) if k_n != -1 else '' for k_n in k_samples])
        k_n_text = [data[k_n] if k_n != -1 else '' for k_n in k_samples]
        
        #q_line = q_text + '\t' + q_n_text
        #k_line = k_text + '\t' + k_n_text
        
        #fout.write(q_line+'\t'+k_line+'\n')
        fout.write(json.dumps({
            'q_text':q_text,
            'q_n_text':q_n_text,
            'k_text':k_text,
            'k_n_text':k_n_text,
        })+'\n')

100%|██████████| 206612/206612 [00:21<00:00, 9598.93it/s] 


In [ ]:
# save side files
pickle.dump([sample_neighbor_num],open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/neighbor_sampling.pkl','wb'))

In [ ]:
# save neighbor file
pickle.dump(train_neighbor,open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/neighbor/train_neighbor.pkl','wb'))
pickle.dump(val_neighbor,open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/neighbor/val_neighbor.pkl','wb'))
pickle.dump(test_neighbor,open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/neighbor/test_neighbor.pkl','wb'))

In [ ]:
# save node labels
random.seed(0)

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_classification.jsonl','w') as fout:
    for q in tqdm(ref_paper):
        
        # prepare sample pool for item
        q_n_pool = set(deepcopy(train_neighbor[q]))

        q_n_pool = list(q_n_pool)
        # random.shuffle(q_n_pool)
        
        # sample neighbor
        if len(q_n_pool) >= sample_neighbor_num:
            q_samples = q_n_pool[:sample_neighbor_num]
        else:
            q_samples = q_n_pool + [-1] * (sample_neighbor_num-len(q_n_pool))
        
        # prepare for writing file
        q_text = data[q]
        #q_n_text = '\*\*'.join([text_process(data[q_n]['title']) if q_n != -1 else '' for q_n in q_samples])
        q_n_text = [data[q_n] if q_n != -1 else '' for q_n in q_samples]
        
        label_names_list = np.array(datasets.label_name[ datasets.y[q]]).tolist()
        label_ids_list = str(np.array(datasets.y[q]))
        print(label_ids_list)
        fout.write(json.dumps({
            'q_text':q_text,
            'q_n_text':q_n_text,
            'labels':label_ids_list,
            'label_names':label_names_list
        })+'\n')

  1%|▏         | 2346/169343 [00:00<00:14, 11688.30it/s]

4
5
28
8
27
34
6
4
3
28
24
36
28
22
16
33
34
26
24
19
28
14
28
28
27
33
34
28
28
3
4
16
10
8
16
22
0
24
16
26
3
8
20
2
28
22
19
28
18
28
28
38
31
4
28
26
5
28
24
20
9
9
8
5
16
28
9
34
28
5
33
28
28
39
36
16
26
13
28
2
28
36
19
3
24
4
23
11
34
29
28
26
34
33
24
28
0
5
24
28
6
10
31
33
10
28
34
28
27
8
2
28
4
28
23
22
19
26
28
26
8
8
28
16
28
4
34
16
16
10
38
28
28
8
4
14
28
36
38
27
23
38
19
19
11
31
10
26
22
2
23
28
28
2
24
28
28
2
28
23
28
22
4
8
36
28
32
34
8
28
8
28
23
8
5
28
28
34
19
24
19
9
36
32
14
8
1
8
8
28
21
30
2
1
33
7
24
26
23
8
1
39
19
28
34
31
26
26
28
2
39
20
26
3
28
4
24
26
34
6
36
16
28
31
10
22
7
16
28
28
10
39
30
30
30
10
16
2
26
28
28
37
20
22
24
5
10
32
8
34
24
11
28
24
39
33
8
2
26
2
13
28
29
19
8
8
3
27
13
20
13
28
16
27
16
9
28
16
37
28
16
8
28
2
4
16
16
8
3
16
10
28
4
8
4
16
28
16
18
24
28
28
13
24
26
30
28
8
34
31
6
26
24
28
27
34
28
28
34
4
34
16
30
8
28
16
19
4
38
31
5
30
19
24
26
23
30
30
27
16
36
26
8
4
8
28
24
24
19
8
25
28
27
0
30
26
34
19
16
24
8
19
24


  2%|▏         | 3515/169343 [00:00<00:14, 11057.45it/s]

34
13
16
36
19
34
34
1
34
4
22
16
28
24
34
16
8
30
16
33
8
16
28
24
10
16
34
34
16
29
2
16
5
10
24
24
28
34
32
24
6
16
16
16
9
16
24
34
16
30
28
8
24
30
38
10
16
16
16
24
24
30
24
30
16
16
16
23
16
4
5
31
4
24
24
3
24
16
6
24
24
2
30
16
2
23
16
16
4
30
13
16
16
16
30
10
23
16
34
36
30
30
16
27
27
24
10
8
24
4
16
28
16
27
36
27
16
24
24
28
4
24
34
28
36
15
11
24
28
24
16
24
3
24
27
16
16
25
24
26
24
27
27
24
1
16
24
5
24
2
16
5
13
28
31
16
23
27
16
28
27
4
16
16
27
10
2
18
4
34
34
30
34
24
16
16
27
16
24
16
16
16
34
16
31
28
24
2
10
24
3
31
8
16
16
26
24
16
28
16
8
9
25
16
24
16
8
8
23
24
7
25
28
4
16
27
19
24
8
30
4
24
16
24
24
30
36
16
16
10
16
26
16
24
28
16
28
16
24
30
4
5
26
38
22
28
24
18
24
18
16
24
6
22
16
13
28
4
16
4
34
24
27
11
30
27
2
28
30
16
4
36
16
4
29
16
2
16
16
16
16
18
24
3
4
4
30
23
27
14
23
20
10
36
14
28
5
19
27
10
28
24
21
10
22
28
4
16
9
2
28
24
28
26
22
2
21
31
0
24
14
28
9
37
10
10
10
30
24
2
24
34
28
27
31
30
10
34
2
4
2
13
3
31
24
34
5
4
28
26
10
5
4
28
23
16

  3%|▎         | 5772/169343 [00:00<00:14, 11194.09it/s]

...

24
34
27
9
26
2
16
24
31
28
28
24
23
34
34
10
16
34
34
9
4
28
9
28
9
16
28
36
28
20
27
36
37
33
25
24
27
28
28
24
28
36
16
26
20
26
16
34
26
28
34
10
28
8
28
8
24
16
28
24
30
16
30
39
39
6
26
19
22
1
28
28
16
11
36
34
31
34
16
24
13
36
16
34
4
10
21
28
28
31
28
24
30
24
32
24
26
6
24
24
16
24
24
16
23
34
28
28
28
3
20
2
16
11
10
1
28
38
2
8
20
36
25
28
24
34
34
34
10
24
34
27
30
26
8
5
24
27
27
28
26
4
30
28
10
16
24
31
30
30
30
28
34
16
30
16
9
16
16
33
28
16
9
27
24
2
39
28
24
36
33
10
36
31
39
9
28
8
5
28
10
4
5
34
36
5
10
19
28
22
34
16
28
19
28
37
10
34
33
4
31
7
2
19
28
38
23
6
36
34
16
20
27
37
8
34
10
23
5
2
36
33
8
20
13
16
34
28
4
15
28
30
24
24
24
28
23
23
23
27
24
2
23
4
37
3
24
24
30
2
28
28
36
10
4
28
8
28
37
10
26
30
13
24
20
10
4
2
2
24
24
16
16
16
37
24
16
5
27
24
28
24
5
28
24
28
8
31
33
16
3
28
26
37
28
38
5
16
15
24
16
24
16
2
38
16
8
37
30
16
24
16
26
24
30
28
16
39
34
16
24
34
24
24
16
27
16
30
30
5
5
4
30
30
30
16
30
22
16
30
30
24
4
16
24
16
26
24
27
27
10
25
30

 99%|█████████▊| 167226/169343 [00:14<00:00, 11290.33it/s]

16
34
38
16
16
24
28
16
30
16
4
16
34
16
2
25
26
16
14
28
33
16
28
8
26
16
16
16
30
24
24
16
16
16
31
16
16
24
34
36
13
30
4
10
30
34
27
38
20
24
30
27
4
24
4
16
16
5
5
0
16
16
5
31
10
30
16
24
25
16
30
16
8
13
8
16
9
9
16
24
31
26
28
24
24
8
35
13
5
33
10
16
4
24
28
7
31
24
28
5
28
30
16
34
7
4
16
25
4
16
24
34
30
16
3
35
23
4
24
24
24
24
16
27
6
36
18
26
24
24
30
16
16
3
23
24
18
24
16
16
27
28
28
3
16
9
8
24
16
16
30
30
16
16
16
16
8
16
10
16
24
4
4
4
24
24
5
24
9
24
39
23
16
16
16
16
16
24
27
24
3
24
23
6
10
16
30
1
30
31
28
28
4
4
28
16
24
28
24
34
16
24
26
16
5
10
16
28
4
24
5
3
39
24
8
34
28
24
24
16
27
24
16
16
2
27
16
30
24
5
30
28
16
5
27
16
19
16
20
30
24
16
16
16
16
34
16
30
27
8
30
5
24
4
16
26
28
16
16
39
7
26
16
16
25
25
8
24
37
24
27
24
25
4
32
24
5
27
33
16
16
31
24
2
30
36
24
8
16
24
24
2
17
24
2
23
6
16
4
9
2
24
24
24
16
30
24
30
16
36
24
30
23
34
10
26
34
30
34
28
37
30
8
24
13
36
28
5
16
30
2
8
10
16
30
16
23
28
2
37
28
28
28
28
16
31
16
8
16
4
10
16
37
4
8
10
16
3

100%|██████████| 169343/169343 [00:15<00:00, 11195.29it/s]

24
8
24
4
24
38
28
37
28
9
0
16
37
16
13
23
28
24
19
10
23
28
34
28
28
4
26
34
28
2
28
28
26
28
8
22
5
28
38
16
34
34
0
25
9
16
21
37
23
37
30
10
36
10
36
28
4
28
28
26
19
28
24
16
24
28
28
31
8
37
28
20
39
2
37
9
11
2
28
28
36
16
23
5
22
28
16
37
16
5
2
16
30
22
28
29
5
9
4
24
23
10
34
2
28
16
34
24
19
38
13
26
5
5
31
23
34
28
26
2
8
22
9
8
26
26
28
9
5
28
6
28
26
33
36
16
4
28
4
34
22
23
2
2
38
10
39
1
28
20
28
28
28
23
19
26
28
28
4
28
2
9
13
16
28
36
28
28
31
27
28
8
31
28
10
6
39
36
8
38
28
28
28
8
10
13
24
16
26
30
6
10
7
5
28
28
8
34
28
2
39
38
31
28
26
28
39
24
8
16
8
2
28
24
9
5
28
16
2
33
28
9
24
10
5
22
8
2
23
8
16
28
28
8
28
28
28
24
10
16
28
28
16
10
16
10
28
28
26
4
9
24
28
34
33
37
19
28
34
24
30
30
2
30
28
24
28
28
8
37
16
27
10
23
33
28
19
26
28
25
36
16
28
39
28
32
4
8
24
33
28
9
24
13
26
16
30
28
8
16
28
8
9
6
30
28
16
34
16
16
33
5
5
2
24
30
37
1
16
16
24
16
5
16
28
16
16
9
19
28
8
10
5
28
24
10
28
24
7
24
36
8
28
24
24
34
26
17
24
28
4
27
27
16
24
28
27
26
30
4
4
3

In [ ]:
# generate self constrastive pretraining

corpus_list = []

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/corpus.txt') as f:
    readin = f.readlines()
    for line in tqdm(readin):
        tmp = line.strip().split('\t')
        corpus_list.append(tmp[1])
        
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/self-train/train.text.jsonl','w') as fout:
    for dd in tqdm(corpus_list):
        fout.write(json.dumps({
            'q_text':dd,
            'q_n_text':[''],
            'k_text':dd,
            'k_n_text':[''],
        })+'\n')

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/self-train/val.text.jsonl','w') as fout:
    for dd in tqdm(corpus_list[:int(0.2*len(corpus_list))]):
        fout.write(json.dumps({
            'q_text':dd,
            'q_n_text':[''],
            'k_text':dd,
            'k_n_text':[''],
        })+'\n')
        
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/self-train/test.text.jsonl','w') as fout:
    for dd in tqdm(corpus_list[int(0.8*len(corpus_list)):]):
        fout.write(json.dumps({
            'q_text':dd,
            'q_n_text':[''],
            'k_text':dd,
            'k_n_text':[''],
        })+'\n')

100%|██████████| 33869/33869 [00:00<00:00, 73643.14it/s]


## Generate node classification data for retrieval and reranking

In [ ]:
# write labels into documents.json

labels_dict = []
label_name2id_dict = {i: text for i, text in tqdm(enumerate([datasets.label_name[index] for index in datasets.y]))}
#for lid in label_name_dict:
for lname in label_name2id_dict:
    if lname != 'null':
        labels_dict.append({'id':lname, 'contents':label_name2id_dict[lname]})
json.dump(labels_dict, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/documents.json', 'w'), indent=4)

# with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/documents.txt', 'w') as fout:
#     #for lid in label_name_dict:
#     for lname in label_name2id_dict.values():
#         if lname == 'null':
#             continue
#         fout.write(label_name2id_dict[lname]+'\t'+lname+'\n')
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/documents.txt', 'w') as f:
    for i, text in label_name2id_dict.items():
        f.write(f'{i}\t{text}\n')

169343it [00:00, 2080955.88it/s]


In [ ]:
# generate node query file & ground truth file

docid = 0

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_classification.jsonl') as f, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_text.tsv', 'w') as fout1, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/truth.trec', 'w') as fout2:
    readin = f.readlines()
    for line in tqdm(readin):
        tmp = json.loads(line)
        fout1.write(str(docid) + '\t' + tmp['q_text'] + '\n')
        for label in tmp['labels']:
            fout2.write(str(docid)+' '+str(0)+' '+str(label)+' '+str(1)+'\n')
        docid += 1

100%|██████████| 169343/169343 [00:02<00:00, 68324.30it/s]


In [ ]:
# generate node query file & ground truth file

docid = 0

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_classification.jsonl') as f, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/train.text.jsonl', 'w') as fout1, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/val.text.jsonl', 'w') as fout2, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/test.truth.trec', 'w') as fout3, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/test.node.text.jsonl', 'w') as fout4:
    readin = f.readlines()
    total_len = len(readin)
    for line in tqdm(readin[:int(0.8*total_len)]):
        tmp = json.loads(line)
        for label_name in tmp['label_names']:
            fout1.write(json.dumps({
                'q_text':tmp['q_text'],
                'q_n_text':tmp['q_n_text'],
                'k_text':label_name,
                'k_n_text':[''],
            })+'\n')
        docid += 1
    
    for line in tqdm(readin[int(0.8*total_len):int(0.9*total_len)]):
        tmp = json.loads(line)
        for label_name in tmp['label_names']:
            fout2.write(json.dumps({
                'q_text':tmp['q_text'],
                'q_n_text':tmp['q_n_text'],
                'k_text':label_name,
                'k_n_text':[''],
            })+'\n')
        docid += 1
        
    for line in tqdm(readin[int(0.9*total_len):]):
        tmp = json.loads(line)
        #fout4.write(str(docid) + '\t' + tmp['q_text'] + '\n')
        fout4.write(json.dumps({
                'id': str(docid),
                'text':tmp['q_text'],
                'n_text':tmp['q_n_text']
            })+'\n')
        for label in tmp['labels']:
            fout3.write(str(docid)+' '+str(0)+' '+str(label)+' '+str(1)+'\n')
        docid += 1

100%|██████████| 16935/16935 [00:00<00:00, 30022.20it/s]


In [ ]:
label_name2id_dict = {i: text for i, text in tqdm(enumerate([datasets.label_name[index] for index in datasets.y]))}
label_name2id_dict
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/label.txt', 'w') as f:
    for id, label in label_name2id_dict.items():
        f.write(f'{id}\t{label}\n')

169343it [00:00, 2002227.03it/s]


## Generate Coarse-grained Classification Data

In [ ]:
# 保存标签名到txt文件
with open('labels.txt', 'w') as f:
    for idx in datasets.y:
        label = datasets.label_name[idx]
        f.write(f'{idx}\t{label}\n')

In [49]:
# # read label name dict
coarse_label_id2name = {}
coarse_label_id2idx = {}

with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/labels.txt') as f:
    readin = f.readlines()
    for line in tqdm(readin):
        tmp = line.strip().split('\t')
        # if tmp[2] == '1':
        coarse_label_id2name[tmp[0]] = tmp[1]
        coarse_label_id2idx[tmp[0]] = len(coarse_label_id2idx)
        print(coarse_label_id2idx[tmp[0]])

print(f'Num of unique labels:{len(coarse_label_id2name)};{coarse_label_id2name}')

FileNotFoundError: [Errno 2] No such file or directory: '/home/yuhanli/GLBench/models/alignment/Patton/data/arxiv/labels.txt'

### Take care here, you need to generate data for 8 & 16 respectively.

In [50]:
# generate train/val/test file
# filter out and only use node which has single label

ktrain = 8 # train sample threshold, how many training samples do we have for each class
kdev = 8 # dev sample threshold, how many dev samples do we have for each class
label_samples = defaultdict(list)
train_mask = datasets.train_mask
val_mask = datasets.val_mask
test_mask = datasets.test_mask
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_classification.jsonl') as f:
    readin = f.readlines()
    for line in tqdm(readin):
        tmp = json.loads(line)
        inter_label = list(tmp['labels'])
        print(inter_label)
        # if len(inter_label) == 1:
        label_samples[inter_label[0]].append(tmp)
print(label_samples)
# select labels
# coarse_label_id2idx = {}
# for l in label_samples:
#     if len(label_samples[l]) > ktrain + kdev:
#         coarse_label_id2idx[l] = len(coarse_label_id2idx)
        
# print(f'Num of unique labels:{len(coarse_label_id2idx)};{coarse_label_id2idx}')

  5%|▍         | 7679/169343 [00:00<00:04, 37998.05it/s]

['4']
['5']
['2', '8']
['8']
['2', '7']
['3', '4']
['6']
['4']
['3']
['2', '8']
['2', '4']
['3', '6']
['2', '8']
['2', '2']
['1', '6']
['3', '3']
['3', '4']
['2', '6']
['2', '4']
['1', '9']
['2', '8']
['1', '4']
['2', '8']
['2', '8']
['2', '7']
['3', '3']
['3', '4']
['2', '8']
['2', '8']
['3']
['4']
['1', '6']
['1', '0']
['8']
['1', '6']
['2', '2']
['0']
['2', '4']
['1', '6']
['2', '6']
['3']
['8']
['2', '0']
['2']
['2', '8']
['2', '2']
['1', '9']
['2', '8']
['1', '8']
['2', '8']
['2', '8']
['3', '8']
['3', '1']
['4']
['2', '8']
['2', '6']
['5']
['2', '8']
['2', '4']
['2', '0']
['9']
['9']
['8']
['5']
['1', '6']
['2', '8']
['9']
['3', '4']
['2', '8']
['5']
['3', '3']
['2', '8']
['2', '8']
['3', '9']
['3', '6']
['1', '6']
['2', '6']
['1', '3']
['2', '8']
['2']
['2', '8']
['3', '6']
['1', '9']
['3']
['2', '4']
['4']
['2', '3']
['1', '1']
['3', '4']
['2', '9']
['2', '8']
['2', '6']
['3', '4']
['3', '3']
['2', '4']
['2', '8']
['0']
['5']
['2', '4']
['2', '8']
['6']
['1', '0']
['3', '1']
['

  9%|▉         | 15806/169343 [00:00<00:03, 39549.17it/s]

['3', '1']
['2', '3']
['2', '4']
['3', '6']
['2', '4']
['6']
['2', '8']
['2', '8']
['3', '4']
['2', '8']
['3', '4']
['8']
['2', '3']
['5']
['5']
['5']
['3', '4']
['1', '6']
['9']
['2', '0']
['2', '8']
['0']
['1', '6']
['6']
['2', '8']
['1', '0']
['3', '4']
['3', '0']
['5']
['3', '4']
['8']
['2', '8']
['2', '8']
['2', '8']
['2', '0']
['3', '9']
['2', '8']
['2', '3']
['2', '7']
['2', '8']
['3']
['2', '8']
['3', '1']
['9']
['1', '0']
['2', '4']
['2']
['2']
['1', '0']
['2', '8']
['2', '4']
['3']
['3', '0']
['1', '6']
['3', '4']
['4']
['4']
['8']
['2', '8']
['2', '0']
['3', '0']
['1', '0']
['1', '3']
['3', '9']
['2', '8']
['9']
['3', '4']
['3', '4']
['1', '3']
['2', '4']
['2', '6']
['1', '0']
['3', '9']
['2', '4']
['2']
['1', '6']
['1', '3']
['2', '8']
['3', '9']
['2', '8']
['3', '4']
['8']
['2', '8']
['3', '4']
['3', '6']
['2', '8']
['9']
['2', '8']
['5']
['2', '7']
['2', '4']
['2', '6']
['2', '8']
['2', '4']
['2', '8']
['8']
['2']
['2', '8']
['1', '0']
['2', '8']
['1', '6']
['2', '8']
['4

 15%|█▌        | 25633/169343 [00:00<00:03, 45444.54it/s]

...

['3', '0']
['3', '6']
['1', '9']
['1', '5']
['1', '6']
['1', '6']
['3', '1']
['2', '4']
['5']
['8']
['8']
['1', '6']
['1', '6']
['3', '4']
['8']
['1', '6']
['2', '9']
['1', '1']
['3', '2']
['2', '8']
['2', '8']
['8']
['2', '4']
['2', '5']
['2', '8']
['1', '6']
['3', '1']
['2', '7']
['3', '4']
['1', '9']
['3', '8']
['3', '3']
['2', '0']
['2', '8']
['1', '6']
['3', '4']
['3', '4']
['5']
['2', '6']
['2', '4']
['8']
['8']
['1']
['9']
['1', '0']
['8']
['2', '8']
['2', '2']
['1', '0']
['2', '6']
['2', '8']
['3', '4']
['9']
['8']
['1', '6']
['2', '8']
['3', '0']
['3', '4']
['5']
['2', '4']
['9']
['2', '8']
['1', '0']
['1', '6']
['2', '8']
['3', '0']
['2', '6']
['3', '0']
['3', '6']
['3', '0']
['3', '4']
['3', '1']
['5']
['3', '0']
['1', '0']
['1', '0']
['5']
['2', '8']
['2', '8']
['2', '6']
['2', '2']
['2']
['8']
['6']
['2', '8']
['2', '7']
['1', '6']
['1', '0']
['2', '7']
['5']
['2', '4']
['5']
['3', '9']
['2', '8']
['1', '6']
['3', '6']
['8']
['1', '6']
['1', '6']
['2', '4']
['3', '8']
['2'

 95%|█████████▌| 161199/169343 [00:05<00:00, 41674.64it/s]

['2', '7']
['5']
['3']
['1', '6']
['3', '4']
['1', '0']
['4']
['1', '9']
['2', '3']
['2', '7']
['8']
['3', '0']
['4']
['2', '8']
['2', '8']
['1']
['1', '6']
['2', '8']
['2', '8']
['1', '6']
['2', '6']
['2', '3']
['1', '6']
['2', '4']
['2', '8']
['3', '4']
['1', '6']
['1', '6']
['3', '4']
['4']
['3', '0']
['3', '0']
['8']
['6']
['3', '3']
['2', '3']
['1', '6']
['9']
['2', '8']
['2', '4']
['1', '6']
['2', '4']
['2', '8']
['8']
['2', '7']
['2', '4']
['5']
['1', '6']
['2', '8']
['2', '4']
['2']
['4']
['3', '0']
['7']
['4']
['1', '6']
['2', '8']
['3', '7']
['2', '6']
['1', '6']
['3', '0']
['2', '8']
['7']
['2', '0']
['3', '4']
['2', '5']
['1', '6']
['2', '4']
['2', '6']
['2', '5']
['1']
['1', '6']
['1', '7']
['1', '0']
['1', '3']
['2']
['3', '8']
['3', '1']
['3', '8']
['5']
['2', '8']
['1', '0']
['1', '3']
['8']
['3', '4']
['2', '8']
['3', '6']
['3', '8']
['1', '6']
['1', '6']
['1', '6']
['2', '6']
['2', '4']
['3', '9']
['1', '6']
['3', '0']
['1']
['2', '3']
['1', '3']
['2', '7']
['2', '4']

100%|██████████| 169343/169343 [00:05<00:00, 31629.62it/s]

['2']
['1', '6']
['2', '6']
['2', '9']
['1', '0']
['2', '8']
['8']
['2', '8']
['2', '7']
['3', '6']
['2']
['3', '4']
['1', '3']
['3', '1']
['3', '4']
['1', '6']
['2', '8']
['1', '6']
['1', '1']
['1', '6']
['1', '3']
['2', '2']
['2', '8']
['2', '4']
['0']
['4']
['5']
['2', '4']
['2', '8']
['2', '6']
['2', '8']
['1', '0']
['2', '6']
['2', '2']
['3', '4']
['2', '8']
['3', '0']
['2', '4']
['3', '0']
['1', '4']
['5']
['3', '7']
['3', '4']
['2', '8']
['2', '0']
['3', '4']
['2', '4']
['2', '8']
['2', '8']
['5']
['1', '6']
['2', '2']
['2', '8']
['3', '8']
['3', '4']
['2', '3']
['3', '4']
['1', '6']
['9']
['1', '0']
['3', '6']
['8']
['1', '6']
['3', '6']
['3', '7']
['2', '8']
['8']
['2', '8']
['2', '0']
['2', '2']
['1', '6']
['2', '1']
['2', '8']
['2', '7']
['1', '6']
['3', '9']
['3', '7']
['3', '0']
['2', '5']
['2', '7']
['1', '6']
['1', '9']
['1', '0']
['2', '8']
['1', '0']
['2', '8']
['1', '6']
['2', '8']
['5']
['7']
['1', '0']
['3', '1']
['5']
['8']
['8']
['2', '8']
['3', '0']
['1', '5']
['

In [ ]:
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_classification.jsonl') as f:
    data = f.readlines()
    print(data[0])

{"q_text": " Stochastic pro-positionalization of non-determinate background knowledge. : It is a well-known fact that propositional learning algorithms require \"good\" features to perform well in practice. So a major step in data engineering for inductive learning is the construction of good features by domain experts. These features often represent properties of structured objects, where a property typically is the occurrence of a certain substructure having certain properties. To partly automate the process of \"feature engineering\", we devised an algorithm that searches for features which are defined by such substructures. The algorithm stochastically conducts a top-down search for first-order clauses, where each clause represents a binary feature. It differs from existing algorithms in that its search is not class-blind, and that it is capable of considering clauses (\"context\") of almost arbitrary length (size). Preliminary experiments are favorable, and support the view that t

In [ ]:
# save
if len(train_mask)==10:
    train_mask = train_mask[0]
    val_mask = val_mask[0]
    test_mask = test_mask[0]

if not os.path.exists(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/{str(ktrain)}_{str(kdev)}'):
    os.mkdir(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/{str(ktrain)}_{str(kdev)}')
train_data = []
dev_data = []
test_data = []
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc/node_classification.jsonl') as f:
    for idx,line in enumerate(f):
        json_obj = json.loads(line)
        if train_mask[idx]:
            train_data.append(json_obj)
        elif val_mask[idx]:
            dev_data.append(json_obj)
        elif test_mask[idx]:
            test_data.append(json_obj)
print(type(train_data[0]['labels']))
    # for idx, d in enumerate(data):
    
        # d = json.loads(d)
    #     if train_mask[idx]:
    #         train_data.append(d)
    #     elif val_mask[idx]:
    #         dev_data.append(d)
    #     elif test_mask[idx]:
    #         test_data.append(d)
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/{str(ktrain)}_{str(kdev)}/train.text.jsonl', 'w') as fout1, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/{str(ktrain)}_{str(kdev)}/val.text.jsonl', 'w') as fout2, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/{str(ktrain)}_{str(kdev)}/test.text.jsonl', 'w') as fout3:
    

    # 写入训练数据
    for idx,d in enumerate(train_data):
        fout1.write(json.dumps({
            'q_text': d['q_text'],
            'q_n_text': d['q_n_text'],
            'label': int(d['labels'])  
            
        }) + '\n')

    # 写入验证数据()
    for idx,d in enumerate (dev_data):
        fout2.write(json.dumps({
            'q_text': d['q_text'],
            'q_n_text': d['q_n_text'],
            'label': int(d['labels'])            
        }) + '\n')

    # # 写入测试数据
    for idx,d in enumerate (test_data):
        fout3.write(json.dumps({
            'q_text': d['q_text'],
            'q_n_text': d['q_n_text'],
            'label': int(d['labels'])            
        }) + '\n')
    # for d in test_data:
    #     fout3.write(json.dumps({
    #         'q_text': d['q_text'],
    #         'q_n_text': d['q_n_text'],
    #         'label': coarse_label_id2idx[l]
    #     }) + '\n')
    # for l in coarse_label_id2idx:
    #     train_data = label_samples[l][:ktrain]
    #     dev_data = label_samples[l][ktrain:(ktrain+kdev)]
    #     #test_data = label_samples[l][(ktrain+kdev):]
    #     test_data = label_samples[l][32:]
    
    #     # write train
    #     for d in train_data:
    #         fout1.write(json.dumps({
    #             'q_text':d['q_text'],
    #             'q_n_text':d['q_n_text'],
    #             'label':coarse_label_id2idx[l]
    #         })+'\n')
    
    #     # write dev
    #     for d in dev_data:
    #         fout2.write(json.dumps({
    #             'q_text':d['q_text'],
    #             'q_n_text':d['q_n_text'],
    #             'label':coarse_label_id2idx[l]
    #         })+'\n')
    
    #     # write test
    #     for d in test_data:
    #         fout3.write(json.dumps({
    #             'q_text':d['q_text'],
    #             'q_n_text':d['q_n_text'],
    #             'label':coarse_label_id2idx[l]
    #         })+'\n')

pickle.dump(coarse_label_id2idx, open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/coarse_label_id2idx.pkl', 'wb'))
pickle.dump([ktrain, kdev], open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/threshold.pkl', 'wb'))

<class 'str'>


In [ ]:
datasets.label_name

In [ ]:
ktrain = 8 # train sample threshold, how many training samples do we have for each class
kdev = 8 #
with open(f'/home/yuhanli/GLBench/models/alignment/Patton/data/{dataset}/nc-coarse/{str(ktrain)}_{str(kdev)}/label_name.txt', 'w') as f:
    for label in datasets.label_name:
        f.write(label + '\n')